# Example generation

Includes:
1) Generating with `n` random static and moving sources
2) Generating with sources in specified positions

## Import dependencies

In [1]:
import os
from pathlib import Path

from scipy import stats

from audiblelight import utils
from audiblelight.core import Scene

## Set default values

All of these values can (and should!) be changed in order to experiment with the functionality of `AudibleLight`.

In [2]:
# OUTPUT DIRECTORY
OUTFOLDER = utils.get_project_root() / 'spatial_scenes'
if not os.path.isdir(OUTFOLDER):
    os.makedirs(OUTFOLDER)

In [3]:
# PATHS
FG_FOLDER = utils.get_project_root() / "tests/test_resources/soundevents"
MESH_PATH = utils.get_project_root() / "tests/test_resources/meshes/Oyens.glb"
AMBIENCE_PATH = utils.get_project_root() / "tests/test_resources/soundevents/waterTap/95709.wav"
AMBIENCE_NOISE = "white"    # an alternative to specifying a filepath

In [4]:
# SCENE SETTINGS
DURATION = 30.0  # seconds
MIC_ARRAY_NAME = 'ambeovr'    # could also be "eigenmike32"...
MAX_OVERLAP = 3   # maximum number of temporally overlapping sound-events

MICROPHONE_POSITION = [2.5, -1.0, 1.0]  # inside the living room

In [5]:
# SCENE-WIDE DISTRIBUTIONS
MIN_VELOCITY, MAX_VELOCITY = 0.5, 1.5    # meters per second
MIN_SNR, MAX_SNR = 2, 8
MIN_RESOLUTION, MAX_RESOLUTION = 0.25, 2.0    # Hz/IRs per second
REF_DB = -50

In [6]:
# This function simply returns a fresh `Scene` object with the parameters set in the cells above
def create_scene() -> Scene:
    return Scene(
        duration=DURATION,
        mesh_path=Path(MESH_PATH),
        scene_start_dist=stats.uniform(0.0, DURATION - 1),
        event_start_dist=None,
        event_duration_dist=None,
        event_velocity_dist=stats.uniform(MIN_VELOCITY, MAX_VELOCITY),
        event_resolution_dist=stats.uniform(MIN_RESOLUTION, MAX_RESOLUTION),
        snr_dist=stats.uniform(MIN_SNR, MAX_SNR),
        fg_path=Path(FG_FOLDER),
        max_overlap=MAX_OVERLAP,
        ref_db=REF_DB
    )

In [7]:
# These can be changed at will
N_STATIC_EVENTS = 4
N_MOVING_EVENTS = 1

In [ ]:
# Create a fresh scene object
scene = create_scene()

In [9]:
# Add the microphone type we want, at the desired position
scene.add_microphone(microphone_type=MIC_ARRAY_NAME, alias=MIC_ARRAY_NAME, position=MICROPHONE_POSITION)

In [10]:
# Add the correct number of static and moving scenes
for _ in range(N_STATIC_EVENTS):
    scene.add_event(event_type="static")
for _ in range(N_MOVING_EVENTS):
    scene.add_event(event_type="moving")

2025-08-11 18:13:15.836 | INFO     | audiblelight.core:add_event:493 - Event added successfully: Static 'Event' with alias 'event000', audio file '/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents/maleSpeech/93899.wav' (unloaded), and 1 emitters.
2025-08-11 18:13:16.089 | INFO     | audiblelight.core:add_event:493 - Event added successfully: Static 'Event' with alias 'event001', audio file '/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents/maleSpeech/93856.wav' (unloaded), and 1 emitters.
2025-08-11 18:13:16.362 | INFO     | audiblelight.core:add_event:493 - Event added successfully: Static 'Event' with alias 'event002', audio file '/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents/femaleSpeech/236385.wav' (unloaded), and 1 emitters.
2025-08-11 18:13:16.698 | INFO     | audiblelight.core:add_event:493 - Event added successfully: Static 'Event' with alias 'event003', a

In [11]:
# Now add the ambience: this is a mono audio file that will be tiled correctly
scene.add_ambience(filepath=AMBIENCE_PATH)

In [12]:
# Do the generation!
scene.generate(
    audio_path=str(OUTFOLDER / "audio_out_random.wav"),
    metadata_path=str(OUTFOLDER / "metadata_out_random.json"),
)

2025-08-11 18:13:18.431 | INFO     | audiblelight.worldstate:simulate:1623 - Starting simulation with 10 emitters, 1 microphones
2025-08-11 18:14:11.335 | INFO     | audiblelight.worldstate:simulate:1631 - Finished simulation! Overall indirect ray efficiency: 0.997
Rendering event audio...: 100%|██████████| 5/5 [00:11<00:00,  2.33s/it]
2025-08-11 18:14:24.205 | INFO     | audiblelight.synthesize:render_audio_for_all_scene_events:520 - Rendered scene audio in 11.68 seconds.!


The audio file and metadata should now be accessible inside our output folder.

## Add in events at specific positions

Now, we can be a bit more granular, and specify the position for our audio events.

In [7]:
# These dictionaries just contain kwargs passed to `add_event`
#  We define them in a list here so we can pass them in in a loop
SOURCES = [
    # First Event: static emitter
    #  Coordinates are cartesian, in absolute terms
    {
        "event_type": "static",
        "alias": "speech",
        "filepath": FG_FOLDER / "maleSpeech/93853.wav",
        "polar": True,
        "position": [90, 0.0, 0.5],
        "scene_start": 0.0,    # start at the beginning of the scene
        "duration": None,
    },

    # Second Event: moving emitter with linear trajectory
    #  Coordinates are cartesian, in absolute terms
    {
        "event_type": "moving",
        "alias": "music",
        "filepath": FG_FOLDER / "music/000010.mp3",
        "polar": False,
        "position": [2.9, -2.5, 0.3],
        "shape": "random",
        "scene_start": 6.0,    # overlaps with telephone event, below
        "spatial_resolution": 1.0,    # Hz
        "spatial_velocity": 0.5,
        "duration": 5,
    },

    # Third Event: moving emitter with random walk
    #  Coordinates are in polar terms WRT mic
    {
        "event_type": "moving",
        "alias": "telephone",
        "filepath": FG_FOLDER / "telephone/30085.wav",
        "polar": True,
        "position": [0.0, 90.0, 1.0],
        "shape": "linear",
        "scene_start": 5.0,    # start five seconds in
        "spatial_resolution": 1.5,
        "spatial_velocity": 1.0,
        "duration": 2,
    }

    # Add your own here...
]

In [8]:
# Create a fresh scene object
scene = create_scene()

CreateContext: Context created


Material for category 'default' was not found. Using default material instead.


In [9]:
# Add the microphone type we want, at the desired position
scene.clear_microphones()
scene.add_microphone(microphone_type=MIC_ARRAY_NAME, alias=MIC_ARRAY_NAME, position=MICROPHONE_POSITION)

In [10]:
# Clean any events already added to the scene
scene.clear_events()
# Add the sound sources
for source in SOURCES:
    scene.add_event(**source)

2025-08-12 15:52:27.566 | INFO     | audiblelight.core:add_event:549 - Event added successfully: Static 'Event' with alias 'speech', audio file '/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents/maleSpeech/93853.wav' (unloaded), and 1 emitters.
2025-08-12 15:52:27.768 | INFO     | audiblelight.core:add_event:549 - Event added successfully: Moving 'Event' with alias 'music', audio file '/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents/music/000010.mp3' (unloaded), and 6 emitters.
2025-08-12 15:52:33.013 | INFO     | audiblelight.core:add_event:549 - Event added successfully: Moving 'Event' with alias 'telephone', audio file '/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents/telephone/30085.wav' (unloaded), and 4 emitters.


In [12]:
# Now add the ambience: this is a mono audio file that will be tiled correctly
scene.clear_ambience()
scene.add_ambience(noise=AMBIENCE_NOISE)

In [ ]:
# Do the generation!
scene.generate(
    audio_path=str(OUTFOLDER / "audio_out_choice.wav"),
    metadata_path=str(OUTFOLDER / "metadata_out_choice.json"),
)

In [11]:
# Pretty print the metadata JSON
print(repr(scene))

{
    "audiblelight_version": "0.1.0",
    "rlr_audio_propagation_version": "0.0.1",
    "creation_time": "2025-08-12_15:52:36",
    "duration": 30.0,
    "ref_db": -50,
    "max_overlap": 3,
    "fg_path": "/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents",
    "ambience": {},
    "events": {
        "speech": {
            "alias": "speech",
            "filename": "93853.wav",
            "filepath": "/home/huw-cheston/Documents/python_projects/AudibleLight/tests/test_resources/soundevents/maleSpeech/93853.wav",
            "class_id": null,
            "class_label": null,
            "is_moving": false,
            "scene_start": 0.0,
            "scene_end": 0.4876190476190476,
            "event_start": 0.0,
            "event_end": 0.4876190476190476,
            "duration": 0.4876190476190476,
            "snr": 2.084342568564807,
            "sample_rate": 44100.0,
            "spatial_resolution": null,
            "spatial_velocity":

## Visualise the scene

In [14]:
out = scene.state.create_scene(emitter_radius=0.05)
out.show()